In [1]:
from sklearn.linear_model import BayesianRidge
from sklearn.model_selection import KFold, StratifiedKFold
from sklearn.preprocessing import OneHotEncoder, LabelEncoder
from sklearn.metrics import mean_squared_error
from sklearn.metrics import log_loss
from feature_selector import FeatureSelector
import numpy as np 
import pandas as pd 
import lightgbm as lgb
import xgboost as xgb
import gc

In [ ]:
fs = FeatureSelector(data = train_df[list(set(train_df.columns) - set(FEATS_EXCLUDED))], labels = train_df['target'].values)

fs.identify_missing(missing_threshold = 0.12)
fs.identify_collinear(correlation_threshold = 0.98)
fs.identify_zero_importance(task = 'regression', eval_metric = 'rmse', n_iterations = 10, early_stopping = True)
fs.identify_low_importance(cumulative_importance = 0.99)
fs.identify_single_unique()

train_removed = fs.remove(methods = 'all')

feats_to_keep = train_removed.columns
len(feats_to_keep)

In [2]:
df_data = pd.read_csv('./datasets/df_data.csv')

# df_nmf_card_merCate_features = pd.read_csv('./datasets/df_nmf_card_merCate_features.csv')
# df_nmf_card_city_features = pd.read_csv('./datasets/df_nmf_card_city_features.csv')
# df_card_merchant_statics = pd.read_csv('./datasets/df_card_merchant_statics.csv')

# df_cardid_vec = pd.read_csv('./datasets/df_cardid_vec.csv')
# df_card_merchant_vec = pd.read_csv('./datasets/df_card_merchant_vec.csv')
# df_card_merchant_vec1 = pd.read_csv('./datasets/df_card_merchant_vec1.csv')

# df_card_city_statics = pd.read_csv('./datasets/df_card_city_statics.csv')

# df_card_merchant_features = pd.read_csv('./datasets/df_card_merchant_features.csv')

In [3]:
# df_data = df_data.merge(df_nmf_card_merCate_features,on='card_id',how='left')
# df_data = df_data.merge(df_nmf_card_city_features,on='card_id',how='left')
# df_data = df_data.merge(df_cardid_vec,on='card_id',how='left')
# df_data = df_data.merge(df_card_merchant_vec1,on='card_id',how='left')
# df_data = df_data.merge(df_card_merchant_vec,on='card_id',how='left')
# df_data = df_data.merge(df_card_merchant_statics,on='card_id',how='left')
# df_data = df_data.merge(df_card_city_statics,on='card_id',how='left')
# df_data = df_data.merge(df_card_merchant_features,on='card_id',how='left')

In [4]:
df_train = df_data[df_data.is_test==0]
df_test = df_data[df_data.is_test==1]

In [5]:
df_train.shape,df_test.shape

((201917, 1174), (123623, 1174))

### 特征选择

In [ ]:
def modeling_cross_validation(df_train,best_cols,lgb_params):
    
    NFOLDS = 10
    kfold = StratifiedKFold(n_splits=NFOLDS,shuffle=True,random_state=2018)
    ntrain = df_train.shape[0]
    ntest = df_test.shape[0]

    oof_train_pred = np.zeros((ntrain,))
    lgb_est = lgb.LGBMRegressor(**lgb_params)
    oof_test_pred = np.zeros((ntest,))
    oof_test_pred_skf = np.empty((NFOLDS, ntest))
    for foldIndex,(dev_index,val_index) in enumerate(kfold.split(df_train,df_train['is_outlier'])):
        x_dev = df_train[best_cols].iloc[dev_index]
        y_dev = df_train[label].iloc[dev_index]
        x_val = df_train[best_cols].iloc[val_index]
        y_val = df_train[label].iloc[val_index]
        lgb_est.fit(x_dev, y_dev,eval_set=[(x_dev,y_dev),(x_val,y_val)],early_stopping_rounds=50,verbose=100)
        oof_train_pred[val_index] = lgb_est.predict(x_val,num_iteration=lgb_est.best_iteration_)
        oof_test_pred_skf[foldIndex,:] = lgb_est.predict(df_test[best_cols],num_iteration=lgb_est.best_iteration_)
    
    oof_test_pred[:] = oof_test_pred_skf.mean(axis=0)
    score = np.sqrt((np.sum(np.square(oof_train_pred - df_train[label].values.reshape(-1,)))/ntrain))
    
    df_test['target'] = oof_test_pred
    df_sub = df_test[['card_id','target']]
    df_sub.to_csv('./submission/df_lgb_sub_%.4f.csv'%score,index=None)
    
    return score

def featureSelect(init_cols):
    lgb_params={
        'learning_rate': 0.01,
        'objective':'regression',
        'n_estimators':8000,
        'metric':'rmse',
        'num_leaves': 80,
        'verbose': 1,
        "subsample": 0.6,
        'lambda_l1':0.2,
        "colsample_bytree": 0.6,
        "random_state":2016,
        'max_depth': 10,
        'device': 'gpu',
        'gpu_platform_id':1,
        'gpu_device_id': 1,
    }
    best_cols = init_cols.copy()
    best_score = modeling_cross_validation(df_train,best_cols, lgb_params)
    print("初始CV score: {:<8.8f}".format(best_score))
    for f in init_cols:
        best_cols.remove(f)
        score = modeling_cross_validation(df_train,best_cols,lgb_params)
        diff = best_score - score
        print('-'*20)
        if diff > 0.0001:
            print("当前移除特征: {}, CV score: {:<8.8f}, best_score: {:<8.8f}, 有效果,删除！！".format(f,score,best_score))
            best_score = score
        else:
            print("当前移除特征: {}, CV score: {:<8.8f}, best_score: {:<8.8f}, 没效果,保留！！".format(f,score,best_score))
            best_cols.append(f)
    print('-'*20)
    print("优化后CV score: {:<8.8f}".format(best_score))
    
    return best_cols
label = ['target']
df_train['is_outlier'] = (df_train.target<-30).astype(np.int)
dropCols = ['card_id','first_active_month','is_outlier','is_test','target','purchase_date','merchant_id']
tr_features = [_f for _f in df_train.columns if _f not in dropCols and df_train[_f].dtype!='object']
best_features = featureSelect(tr_features)

/home/sjtu123/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:66: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy


Training until validation scores don't improve for 50 rounds.
[100]	training's rmse: 3.56327	valid_1's rmse: 3.71263
[200]	training's rmse: 3.41936	valid_1's rmse: 3.67877
[300]	training's rmse: 3.33347	valid_1's rmse: 3.66734
[400]	training's rmse: 3.27102	valid_1's rmse: 3.66173
[500]	training's rmse: 3.22099	valid_1's rmse: 3.6606
Early stopping, best iteration is:
[547]	training's rmse: 3.2026	valid_1's rmse: 3.66
Training until validation scores don't improve for 50 rounds.
[100]	training's rmse: 3.56323	valid_1's rmse: 3.72116
[200]	training's rmse: 3.41802	valid_1's rmse: 3.69134
[300]	training's rmse: 3.32913	valid_1's rmse: 3.67981
[400]	training's rmse: 3.2679	valid_1's rmse: 3.67539
[500]	training's rmse: 3.21941	valid_1's rmse: 3.67401
Early stopping, best iteration is:
[490]	training's rmse: 3.22357	valid_1's rmse: 3.67378
Training until validation scores don't improve for 50 rounds.
[100]	training's rmse: 3.56235	valid_1's rmse: 3.72185
[200]	training's rmse: 3.42004	vali

/home/sjtu123/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:24: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy


初始CV score: 3.65781472
Training until validation scores don't improve for 50 rounds.
[100]	training's rmse: 3.56164	valid_1's rmse: 3.71266
[200]	training's rmse: 3.42132	valid_1's rmse: 3.67879
[300]	training's rmse: 3.33547	valid_1's rmse: 3.6675
[400]	training's rmse: 3.27299	valid_1's rmse: 3.66331
[500]	training's rmse: 3.22517	valid_1's rmse: 3.66131
[600]	training's rmse: 3.18719	valid_1's rmse: 3.6609
Early stopping, best iteration is:
[573]	training's rmse: 3.19779	valid_1's rmse: 3.66077
Training until validation scores don't improve for 50 rounds.
[100]	training's rmse: 3.56221	valid_1's rmse: 3.72135
[200]	training's rmse: 3.41751	valid_1's rmse: 3.69222
[300]	training's rmse: 3.32987	valid_1's rmse: 3.68179
[400]	training's rmse: 3.26777	valid_1's rmse: 3.67806
[500]	training's rmse: 3.2209	valid_1's rmse: 3.6769
Early stopping, best iteration is:
[526]	training's rmse: 3.21	valid_1's rmse: 3.67669
Training until validation scores don't improve for 50 rounds.
[100]	trainin

/home/sjtu123/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:24: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy


...

--------------------
当前移除特征: new_purcahseDiffStd_2, CV score: 3.65596205, best_score: 3.65496811, 没效果,保留！！
Training until validation scores don't improve for 50 rounds.
[100]	training's rmse: 3.56041	valid_1's rmse: 3.71342
[200]	training's rmse: 3.41825	valid_1's rmse: 3.6791
[300]	training's rmse: 3.33256	valid_1's rmse: 3.66705
[400]	training's rmse: 3.26976	valid_1's rmse: 3.66179
[500]	training's rmse: 3.22062	valid_1's rmse: 3.65996
[600]	training's rmse: 3.18389	valid_1's rmse: 3.65984
Early stopping, best iteration is:
[640]	training's rmse: 3.17216	valid_1's rmse: 3.65937
Training until validation scores don't improve for 50 rounds.
[100]	training's rmse: 3.562	valid_1's rmse: 3.72576
[200]	training's rmse: 3.41646	valid_1's rmse: 3.69651
[300]	training's rmse: 3.32759	valid_1's rmse: 3.68379
[400]	training's rmse: 3.26583	valid_1's rmse: 3.68014
[500]	training's rmse: 3.21805	valid_1's rmse: 3.678
[600]	training's rmse: 3.18297	valid_1's rmse: 3.67781
Early stopping, best ite

/home/sjtu123/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:24: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy


--------------------
当前移除特征: new_dayDiffMax_2, CV score: 3.65750868, best_score: 3.65496811, 没效果,保留！！
Training until validation scores don't improve for 50 rounds.
[100]	training's rmse: 3.56139	valid_1's rmse: 3.71162
[200]	training's rmse: 3.41814	valid_1's rmse: 3.67801
[300]	training's rmse: 3.33332	valid_1's rmse: 3.66747
[400]	training's rmse: 3.26906	valid_1's rmse: 3.66365
[500]	training's rmse: 3.22075	valid_1's rmse: 3.6614
Early stopping, best iteration is:
[519]	training's rmse: 3.21348	valid_1's rmse: 3.66114
Training until validation scores don't improve for 50 rounds.
[100]	training's rmse: 3.5622	valid_1's rmse: 3.71819
[200]	training's rmse: 3.41625	valid_1's rmse: 3.68937
[300]	training's rmse: 3.32861	valid_1's rmse: 3.67893
[400]	training's rmse: 3.26669	valid_1's rmse: 3.67576
[500]	training's rmse: 3.21736	valid_1's rmse: 3.67501
[600]	training's rmse: 3.18082	valid_1's rmse: 3.67474
Early stopping, best iteration is:
[565]	training's rmse: 3.19299	valid_1's rmse:

/home/sjtu123/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:24: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy


--------------------
当前移除特征: new_dayDiffMin_2, CV score: 3.65712630, best_score: 3.65496811, 没效果,保留！！
Training until validation scores don't improve for 50 rounds.
[100]	training's rmse: 3.562	valid_1's rmse: 3.71233
[200]	training's rmse: 3.41844	valid_1's rmse: 3.67937
[300]	training's rmse: 3.33402	valid_1's rmse: 3.6669
[400]	training's rmse: 3.26901	valid_1's rmse: 3.6628
[500]	training's rmse: 3.22169	valid_1's rmse: 3.66039
[600]	training's rmse: 3.18437	valid_1's rmse: 3.65978
Early stopping, best iteration is:
[576]	training's rmse: 3.1929	valid_1's rmse: 3.65956
Training until validation scores don't improve for 50 rounds.
[100]	training's rmse: 3.56255	valid_1's rmse: 3.72376
[200]	training's rmse: 3.41773	valid_1's rmse: 3.69405
[300]	training's rmse: 3.33026	valid_1's rmse: 3.68243
[400]	training's rmse: 3.26643	valid_1's rmse: 3.6776
[500]	training's rmse: 3.21906	valid_1's rmse: 3.67595


### Boruta feature elimination

In [ ]:
from __future__ import print_function, division
from sklearn.utils import check_random_state, check_X_y
from sklearn.base import TransformerMixin, BaseEstimator
from datetime import datetime
import pandas as pd
import numpy as np
import scipy as sp
# from boruta import BorutaPy

def timer(start_time=None):
    if not start_time:
        start_time = datetime.now()
        return start_time
    elif start_time:
        thour, temp_sec = divmod((datetime.now() - start_time).total_seconds(), 3600)
        tmin, tsec = divmod(temp_sec, 60)
        print('\n Time taken: %i hours %i minutes and %s seconds.' % (thour, tmin, round(tsec, 2)))

class BorutaPy(BaseEstimator, TransformerMixin):

    def __init__(self, estimator, n_estimators=1000, perc=100, alpha=0.05,
                 two_step=True, max_iter=100, random_state=None, verbose=0):
        self.estimator = estimator
        self.n_estimators = n_estimators
        self.perc = perc
        self.alpha = alpha
        self.two_step = two_step
        self.max_iter = max_iter
        self.random_state = random_state
        self.verbose = verbose

    def fit(self, X, y):
        """
        Fits the Boruta feature selection with the provided estimator.
        Parameters
        ----------
        X : array-like, shape = [n_samples, n_features]
            The training input samples.
        y : array-like, shape = [n_samples]
            The target values.
        """

        return self._fit(X, y)

    def transform(self, X, weak=False):
        """
        Reduces the input X to the features selected by Boruta.
        Parameters
        ----------
        X : array-like, shape = [n_samples, n_features]
            The training input samples.
        weak: boolean, default = False
            If set to true, the tentative features are also used to reduce X.
        Returns
        -------
        X : array-like, shape = [n_samples, n_features_]
            The input matrix X's columns are reduced to the features which were
            selected by Boruta.
        """

        return self._transform(X, weak)

    def fit_transform(self, X, y, weak=False):
        """
        Fits Boruta, then reduces the input X to the selected features.
        Parameters
        ----------
        X : array-like, shape = [n_samples, n_features]
            The training input samples.
        y : array-like, shape = [n_samples]
            The target values.
        weak: boolean, default = False
            If set to true, the tentative features are also used to reduce X.
        Returns
        -------
        X : array-like, shape = [n_samples, n_features_]
            The input matrix X's columns are reduced to the features which were
            selected by Boruta.
        """

        self._fit(X, y)
        return self._transform(X, weak)

    def _fit(self, X, y):
        # check input params
        self._check_params(X, y)
        self.random_state = check_random_state(self.random_state)
        # setup variables for Boruta
        n_sample, n_feat = X.shape
        _iter = 1
        # holds the decision about each feature:
        # 0  - default state = tentative in original code
        # 1  - accepted in original code
        # -1 - rejected in original code
        dec_reg = np.zeros(n_feat, dtype=np.int)
        # counts how many times a given feature was more important than
        # the best of the shadow features
        hit_reg = np.zeros(n_feat, dtype=np.int)
        # these record the history of the iterations
        imp_history = np.zeros(n_feat, dtype=np.float)
        sha_max_history = []

        # set n_estimators
        if self.n_estimators != 'auto':
            self.estimator.set_params(n_estimators=self.n_estimators)

        # main feature selection loop
        while np.any(dec_reg == 0) and _iter < self.max_iter:
            # find optimal number of trees and depth
            if self.n_estimators == 'auto':
                # number of features that aren't rejected
                not_rejected = np.where(dec_reg >= 0)[0].shape[0]
                n_tree = self._get_tree_num(not_rejected)
                self.estimator.set_params(n_estimators=n_tree)

            # make sure we start with a new tree in each iteration
            self.estimator.set_params(random_state=self.random_state.get_state()[2])

            # add shadow attributes, shuffle them and train estimator, get imps
            cur_imp = self._add_shadows_get_imps(X, y, dec_reg)

            # get the threshold of shadow importances we will use for rejection
            imp_sha_max = np.percentile(cur_imp[1], self.perc)

            # record importance history
            sha_max_history.append(imp_sha_max)
            imp_history = np.vstack((imp_history, cur_imp[0]))

            # register which feature is more imp than the max of shadows
            hit_reg = self._assign_hits(hit_reg, cur_imp, imp_sha_max)

            # based on hit_reg we check if a feature is doing better than
            # expected by chance
            dec_reg = self._do_tests(dec_reg, hit_reg, _iter)

            # print out confirmed features
            if self.verbose > 0 and _iter < self.max_iter:
                self._print_results(dec_reg, _iter, 0)
            if _iter < self.max_iter:
                _iter += 1

        # we automatically apply R package's rough fix for tentative ones
        confirmed = np.where(dec_reg == 1)[0]
        tentative = np.where(dec_reg == 0)[0]
        # ignore the first row of zeros
        tentative_median = np.median(imp_history[1:, tentative], axis=0)
        # which tentative to keep
        tentative_confirmed = np.where(tentative_median
                                       > np.median(sha_max_history))[0]
        tentative = tentative[tentative_confirmed]

        # basic result variables
        self.n_features_ = confirmed.shape[0]
        self.support_ = np.zeros(n_feat, dtype=np.bool)
        self.support_[confirmed] = 1
        self.support_weak_ = np.zeros(n_feat, dtype=np.bool)
        self.support_weak_[tentative] = 1

        # ranking, confirmed variables are rank 1
        self.ranking_ = np.ones(n_feat, dtype=np.int)
        # tentative variables are rank 2
        self.ranking_[tentative] = 2
        # selected = confirmed and tentative
        selected = np.hstack((confirmed, tentative))
        # all rejected features are sorted by importance history
        not_selected = np.setdiff1d(np.arange(n_feat), selected)
        # large importance values should rank higher = lower ranks -> *(-1)
        imp_history_rejected = imp_history[1:, not_selected] * -1

        # update rank for not_selected features
#         if not_selected.shape[0] > 0 and not_selected.shape[1] > 0:
        if not_selected.shape[0] > 0:
                # calculate ranks in each iteration, then median of ranks across feats
            iter_ranks = self._nanrankdata(imp_history_rejected, axis=1)
            rank_medians = np.nanmedian(iter_ranks, axis=0)
            ranks = self._nanrankdata(rank_medians, axis=0)

            # set smallest rank to 3 if there are tentative feats
            if tentative.shape[0] > 0:
                ranks = ranks - np.min(ranks) + 3
            else:
                # and 2 otherwise
                ranks = ranks - np.min(ranks) + 2
            self.ranking_[not_selected] = ranks
        else:
            # all are selected, thus we set feature supports to True
            self.support_ = np.ones(n_feat, dtype=np.bool)

        # notify user
        if self.verbose > 0:
            self._print_results(dec_reg, _iter, 1)
        return self

    def _transform(self, X, weak=False):
        # sanity check
        try:
            self.ranking_
        except AttributeError:
            raise ValueError('You need to call the fit(X, y) method first.')

        if weak:
            X = X[:, self.support_ + self.support_weak_]
        else:
            X = X[:, self.support_]
        return X

    def _get_tree_num(self, n_feat):
        depth = self.estimator.get_params()['max_depth']
        if depth == None:
            depth = 10
        # how many times a feature should be considered on average
        f_repr = 100
        # n_feat * 2 because the training matrix is extended with n shadow features
        multi = ((n_feat * 2) / (np.sqrt(n_feat * 2) * depth))
        n_estimators = int(multi * f_repr)
        return n_estimators

    def _get_imp(self, X, y):
        try:
            self.estimator.fit(X, y)
        except Exception as e:
            raise ValueError('Please check your X and y variable. The provided'
                             'estimator cannot be fitted to your data.\n' + str(e))
        try:
            imp = self.estimator.feature_importances_
        except Exception:
            raise ValueError('Only methods with feature_importance_ attribute '
                             'are currently supported in BorutaPy.')
        return imp

    def _get_shuffle(self, seq):
        self.random_state.shuffle(seq)
        return seq

    def _add_shadows_get_imps(self, X, y, dec_reg):
        # find features that are tentative still
        x_cur_ind = np.where(dec_reg >= 0)[0]
        x_cur = np.copy(X[:, x_cur_ind])
        x_cur_w = x_cur.shape[1]
        # deep copy the matrix for the shadow matrix
        x_sha = np.copy(x_cur)
        # make sure there's at least 5 columns in the shadow matrix for
        while (x_sha.shape[1] < 5):
            x_sha = np.hstack((x_sha, x_sha))
        # shuffle xSha
        x_sha = np.apply_along_axis(self._get_shuffle, 0, x_sha)
        # get importance of the merged matrix
        imp = self._get_imp(np.hstack((x_cur, x_sha)), y)
        # separate importances of real and shadow features
        imp_sha = imp[x_cur_w:]
        imp_real = np.zeros(X.shape[1])
        imp_real[:] = np.nan
        imp_real[x_cur_ind] = imp[:x_cur_w]
        return imp_real, imp_sha

    def _assign_hits(self, hit_reg, cur_imp, imp_sha_max):
        # register hits for features that did better than the best of shadows
        cur_imp_no_nan = [val for val in cur_imp[0] if not np.isnan(val)]
        hits = np.where(cur_imp_no_nan > imp_sha_max)[0]
        hit_reg[hits] += 1
        return hit_reg

    def _do_tests(self, dec_reg, hit_reg, _iter):
        active_features = np.where(dec_reg >= 0)[0]
        hits = hit_reg[active_features]
        # get uncorrected p values based on hit_reg
        to_accept_ps = sp.stats.binom.sf(hits - 1, _iter, .5).flatten()
        to_reject_ps = sp.stats.binom.cdf(hits, _iter, .5).flatten()

        if self.two_step:
            # two step multicor process
            # first we correct for testing several features in each round using FDR
            to_accept = self._fdrcorrection(to_accept_ps, alpha=self.alpha)[0]
            to_reject = self._fdrcorrection(to_reject_ps, alpha=self.alpha)[0]

            # second we correct for testing the same feature over and over again
            # using bonferroni
            to_accept2 = to_accept_ps <= self.alpha / float(_iter)
            to_reject2 = to_reject_ps <= self.alpha / float(_iter)

            # combine the two multi corrections, and get indexes
            to_accept *= to_accept2
            to_reject *= to_reject2
        else:
            # as in th original Boruta, we simply do bonferroni correction
            # with the total n_feat in each iteration
            to_accept = to_accept_ps <= self.alpha / float(len(dec_reg))
            to_reject = to_reject_ps <= self.alpha / float(len(dec_reg))

        # find features which are 0 and have been rejected or accepted
        to_accept = np.where((dec_reg[active_features] == 0) * to_accept)[0]
        to_reject = np.where((dec_reg[active_features] == 0) * to_reject)[0]

        # updating dec_reg
        dec_reg[active_features[to_accept]] = 1
        dec_reg[active_features[to_reject]] = -1
        return dec_reg

    def _fdrcorrection(self, pvals, alpha=0.05):
        """
            Benjamini/Hochberg p-value correction for false discovery rate, from
            statsmodels package. Included here for decoupling dependency on statsmodels.
            Parameters
            ----------
            pvals : array_like
                set of p-values of the individual tests.
            alpha : float
                error rate
            Returns
            -------
            rejected : array, bool
                True if a hypothesis is rejected, False if not
            pvalue-corrected : array
                pvalues adjusted for multiple hypothesis testing to limit FDR
        """
        pvals = np.asarray(pvals)
        pvals_sortind = np.argsort(pvals)
        pvals_sorted = np.take(pvals, pvals_sortind)
        nobs = len(pvals_sorted)
        ecdffactor = np.arange(1, nobs + 1) / float(nobs)

        reject = pvals_sorted <= ecdffactor * alpha
        if reject.any():
            rejectmax = max(np.nonzero(reject)[0])
            reject[:rejectmax] = True

        pvals_corrected_raw = pvals_sorted / ecdffactor
        pvals_corrected = np.minimum.accumulate(pvals_corrected_raw[::-1])[::-1]
        pvals_corrected[pvals_corrected > 1] = 1
        # reorder p-values and rejection mask to original order of pvals
        pvals_corrected_ = np.empty_like(pvals_corrected)
        pvals_corrected_[pvals_sortind] = pvals_corrected
        reject_ = np.empty_like(reject)
        reject_[pvals_sortind] = reject
        return reject_, pvals_corrected_

    def _nanrankdata(self, X, axis=1):
        """
            Replaces bottleneck's nanrankdata with scipy and numpy alternative.
        """
        ranks = sp.stats.mstats.rankdata(X, axis=axis)
        ranks[np.isnan(X)] = np.nan
        return ranks

    def _check_params(self, X, y):
        """
            Check hyperparameters as well as X and y before proceeding with fit.
        """
        # check X and y are consistent len, X is Array and y is column
        X, y = check_X_y(X, y)
        if self.perc <= 0 or self.perc > 100:
            raise ValueError('The percentile should be between 0 and 100.')

        if self.alpha <= 0 or self.alpha > 1:
            raise ValueError('Alpha should be between 0 and 1.')

    def _print_results(self, dec_reg, _iter, flag):
        n_iter = str(_iter) + ' / ' + str(self.max_iter)
        n_confirmed = np.where(dec_reg == 1)[0].shape[0]
        n_rejected = np.where(dec_reg == -1)[0].shape[0]
        cols = ['Iteration: ', 'Confirmed: ', 'Tentative: ', 'Rejected: ']

        # still in feature selection
        if flag == 0:
            n_tentative = np.where(dec_reg == 0)[0].shape[0]
            content = map(str, [n_iter, n_confirmed, n_tentative, n_rejected])
            if self.verbose == 1:
                output = cols[0] + n_iter
            elif self.verbose > 1:
                output = '\n'.join([x[0] + '\t' + x[1] for x in zip(cols, content)])

        # Boruta finished running and tentatives have been filtered
        else:
            n_tentative = np.sum(self.support_weak_)
            content = map(str, [n_iter, n_confirmed, n_tentative, n_rejected])
            result = '\n'.join([x[0] + '\t' + x[1] for x in zip(cols, content)])
            output = "\n\nBorutaPy finished running.\n\n" + result
        print(output)

In [ ]:
df_data = pd.read_csv('./datasets/df_data.csv')
df_nmf_card_merCate_features = pd.read_csv('./datasets/df_nmf_card_merCate_features.csv')
df_nmf_card_city_features = pd.read_csv('./datasets/df_nmf_card_city_features.csv')
df_card_merchant_statics = pd.read_csv('./datasets/df_card_merchant_statics.csv')
df_cardid_vec = pd.read_csv('./datasets/df_cardid_vec.csv')
df_card_merchant_vec = pd.read_csv('./datasets/df_card_merchant_vec.csv')
df_card_city_statics = pd.read_csv('./datasets/df_card_city_statics.csv')
df_card_merchant_features = pd.read_csv('./datasets/df_card_merchant_features.csv')

In [ ]:
df_data = df_data.merge(df_nmf_card_merCate_features,on='card_id',how='left')
df_data = df_data.merge(df_nmf_card_city_features,on='card_id',how='left')
df_data = df_data.merge(df_cardid_vec,on='card_id',how='left')
df_data = df_data.merge(df_card_merchant_vec,on='card_id',how='left')
df_data = df_data.merge(df_card_merchant_statics,on='card_id',how='left')
df_data = df_data.merge(df_card_city_statics,on='card_id',how='left')
df_data = df_data.merge(df_card_merchant_features,on='card_id',how='left')

In [ ]:
df_train = df_data[df_data.is_test==0]
df_test = df_data[df_data.is_test==1]

In [ ]:
label = ['target']
dropCols = ['card_id','first_active_month','is_outlier','is_test','target','purchase_date','merchant_id']
tr_features = [_f for _f in df_train.columns if _f not in dropCols and df_train[_f].dtype!='object']

print(df_data[tr_features].shape)

In [ ]:
df_data.fillna(0,inplace=True)

df_data.replace([np.inf,-np.inf],0,inplace=True)

In [ ]:
from functionUtils import *
df_data = reduce_mem_usage(df_data)

In [ ]:

lgb_params={
    'boosting_type':'rf',
    'learning_rate': 0.01,
    'objective':'regression',
    'n_estimators':8000,
    'metric':'rmse',
    'num_leaves': 60,
    'verbose': 1,
    'bagging_freq':1,
    'bagging_fraction':0.8,
    'bagging_seed':11,
    "subsample": 0.6,
    'random_state':42,
    'lambda_l1':0.2,
    "colsample_bytree": 0.6,
    'max_depth': 7,
    'n_jobs':16,
    'device': 'gpu',
    'gpu_platform_id':1,
    'gpu_device_id': 1,
}
X_train = df_train[tr_features].values
y_train = df_train.target.values
lgb_est = lgb.LGBMRegressor(**lgb_params)
feature_selector = BorutaPy(lgb_est,n_estimators=8000, max_iter=1000,verbose=2,random_state=2018)

feature_selector.fit(X_train, y_train)


In [ ]:
# number of selected features
print ('\n Number of selected features:')
print (feature_selector.n_features_)

feature_df = pd.DataFrame(df_train[tr_features].columns.tolist(), columns=['features'])
feature_df['rank']=feature_selector.ranking_
feature_df = feature_df.sort_values('rank', ascending=True).reset_index(drop=True)
print ('\n Top %d features:' % feature_selector.n_features_)
print (feature_df.head(feature_selector.n_features_))
# feature_df.to_csv('boruta-feature-ranking.csv', index=False)

# check ranking of features
print ('\n Feature ranking:')
print (feature_selector.ranking_)